In [1]:
import pandas as pd
import folium
from folium.plugins import TimestampedGeoJson
from datetime import datetime, timedelta
import json

# Step 1: Load and prepare data
data = pd.read_csv("12.19.24_chattadata_vehicle_data.csv")
data["Incident Date"] = pd.to_datetime(data["Incident Date"])
ninety_days_ago = datetime.now() - timedelta(days=90)
data_last_period = data[data["Incident Date"] >= ninety_days_ago]

# Step 2: Create the base map
m = folium.Map(location=[35.0456, -85.3097], zoom_start=12)

# Add a more concise info box
title_html = """
<div style="position: fixed; 
            top: 10px; 
            left: 50px; 
            width: 200px; 
            height: auto; 
            z-index:9999; 
            font-size:12px;
            background-color: white;
            padding: 8px;
            border-radius: 5px;
            border: 2px solid gray;
            opacity: 0.9;">
    <h4 style="margin-top: 0; margin-bottom: 5px; color: #333; font-size: 14px;">Traffic Incidents Map</h4>
    <div style="font-size: 11px; margin: 5px 0;">
        Use time slider (bottom) or play button to view incidents by date. Click markers for details.
    </div>
    <div style="margin-top: 5px; border-top: 1px solid #ccc; padding-top: 5px; font-size: 11px;">
        <i class="fa fa-exclamation-triangle" style="color: red;"></i> Fatal Accident<br>
        <i class="fa fa-plus-square" style="color: orange;"></i> Injury Accident<br>
        <i class="fa fa-car" style="color: blue;"></i> Property Damage
    </div>
</div>
"""


# Add the title HTML to the map
m.get_root().html.add_child(folium.Element(title_html))

# Add a custom CSS style to improve the layer control appearance
css = """
<style>
.leaflet-control-layers {
    background: rgba(255, 255, 255, 0.9);
    border-radius: 5px;
    box-shadow: 0 0 15px rgba(0,0,0,0.2);
}
.leaflet-control-layers-toggle {
    background-color: white;
}
.leaflet-popup-content {
    font-family: Arial, sans-serif;
    font-size: 12px;
}
</style>
"""
m.get_root().html.add_child(folium.Element(css))

# Step 3: Define incident types with colors and symbols
incident_types = {
    "Fatal": {
        "color": "red",
        "condition": lambda x: x == "Fatal",
        "icon": "exclamation-triangle",
        "size": "12px",
    },
    "Injury": {
        "color": "orange",
        "condition": lambda x: "Injury" in str(x),
        "icon": "plus-square",
        "size": "12px",
    },
    "Property": {
        "color": "blue",
        "condition": lambda x: "Property" in str(x),
        "icon": "car",
        "size": "12px",
    },
}


# Create custom div icon HTML template
def create_icon_html(icon_name, color, size):
    return f"""
        <div style="text-align: center;">
            <i class="fa fa-{icon_name}" style="color: {color}; font-size: {size};"></i>
        </div>
    """


# Step 4: Prepare features for TimestampedGeoJson
features = []
for _, row in data_last_period.iterrows():
    # Determine incident type and styling
    incident_style = {"color": "gray", "radius": 9}  # default
    for incident_type, info in incident_types.items():
        if info["condition"](row["Accident Type"]):
            incident_style = {"color": info["color"], "radius": 5, "icon": info["icon"]}
            break

    feature = {
        "type": "Feature",
        "geometry": {
            "type": "Point",
            "coordinates": [row["Longitude"], row["Latitude"]],
        },
        "properties": {
            "time": row["Incident Date"].strftime("%Y-%m-%d"),
            "icon": "circle",
            "style": {
                "color": incident_style["color"],
                "fillColor": incident_style["color"],
                "fillOpacity": 0.7,
                "weight": 1,
                "radius": incident_style["radius"],
            },
            "popup": f"""
                <b>Incident Date:</b> {row['Incident Date']}<br>
                <b>Street:</b> {row['Street']}<br>
                <b>Intersection:</b> {row['Intersection']}<br>
                <b>Accident Type:</b> {row['Accident Type']}<br>
                <b>Collision Type:</b> {row['Collision Type']}<br>
            """,
        },
    }
    features.append(feature)

# Create TimestampedGeoJson layer
timestamped_layer = TimestampedGeoJson(
    {"type": "FeatureCollection", "features": features},
    period="P1D",
    add_last_point=False,
    auto_play=True,
    loop=False,
    max_speed=1,
    loop_button=True,
    date_options="YYYY-MM-DD",
    time_slider_drag_update=True,
    duration="P1D",
)
timestamped_layer.add_to(m)

# Step 5: Add static incident group markers with divIcons
incident_groups = {
    f'<i class="fa fa-exclamation-triangle" style="color: red;"></i> Fatal Accidents': {
        "color": "red",
        "data": data_last_period[data_last_period["Accident Type"] == "Fatal"],
        "icon": "exclamation-triangle",
    },
    f'<i class="fa fa-plus-square" style="color: orange;"></i> Injury Accidents': {
        "color": "orange",
        "data": data_last_period[
            data_last_period["Accident Type"].str.contains("Injury", na=False)
        ],
        "icon": "plus-square",
    },
    f'<i class="fa fa-car" style="color: blue;"></i> Property Damage': {
        "color": "blue",
        "data": data_last_period[
            data_last_period["Accident Type"].str.contains("Property", na=False)
        ],
        "icon": "car",
    },
}


# Add markers for each incident type
for incident_type, group_info in incident_groups.items():
    fg = folium.FeatureGroup(name=incident_type)

    for _, row in group_info["data"].iterrows():
        details = f"""
        <b>Incident Date:</b> {row['Incident Date']}<br>
        <b>Street:</b> {row['Street']}<br>
        <b>Intersection:</b> {row['Intersection']}<br>
        <b>Accident Type:</b> {row['Accident Type']}<br>
        <b>Collision Type:</b> {row['Collision Type']}<br>
        """

        # Create custom div icon
        icon_html = create_icon_html(group_info["icon"], group_info["color"], "12px")
        icon = folium.DivIcon(html=icon_html)

        folium.Marker(
            location=[row["Latitude"], row["Longitude"]],
            popup=folium.Popup(details, max_width=300),
            icon=icon,
        ).add_to(fg)

    fg.add_to(m)

# Add layer control
folium.LayerControl().add_to(m)

# Save the map
m.save("12.19.24_vehicle_incidents_90_days.html")
m

/var/folders/t8/gtcfgt113_zd8vcxg4xmfxjr0000gp/T/ipykernel_70958/3638126534.py:9: UserWarning: Could not infer format, so each element will be parsed individually, falling back to `dateutil`. To ensure parsing is consistent and as-expected, please specify a format.
  data["Incident Date"] = pd.to_datetime(data["Incident Date"])
